# Run pre-trained DeepSeek Coder 1.3B Model on Chat-GPT 4o generated dataset

## First load dataset into pandas dataframe

In [1]:
import pandas as pd 

# Load dataset and check length
df = pd.read_csv("./train-data/sql_train.tsv", sep='\t')
print("Total dataset examples: " + str(len(df)))
print("\n")

# Test sampling
sample = df.sample(n=1)
print(sample["natural_query"].values[0])
print(sample["sql_query"].values[0])
print(sample["result"].values[0])

Total dataset examples: 1044


What was the largest lead the Golden State Warriors had in a game during the 2018 season?
SELECT MAX(other_stats.largest_lead_home)  FROM other_stats  JOIN game ON other_stats.game_id = game.game_id  WHERE game.team_name_home = 'Golden State Warriors'  AND game.season_id = '22018';
44


## Load pre-trained DeepSeek model using transformers and pytorch packages

In [2]:
from transformers import AutoTokenizer, AutoModelForCausalLM
import torch

# Set device to cuda if available, otherwise CPU
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load model and tokenizer
tokenizer = AutoTokenizer.from_pretrained("./deepseek-coder-1.3b-instruct")
model = AutoModelForCausalLM.from_pretrained("./deepseek-coder-1.3b-instruct", torch_dtype=torch.bfloat16, device_map=device) 

c:\Users\Dean\AppData\Local\Programs\Python\Python312\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


## Create prompt to setup the model for better performance

In [3]:
input_text = """You are an AI assistant that converts natural language queries into valid SQLite queries.
Database Schema and Explanations

team Table
Stores information about NBA teams.
CREATE TABLE IF NOT EXISTS "team" (
  "id" TEXT PRIMARY KEY,      -- Unique identifier for the team
  "full_name" TEXT,           -- Full official name of the team (e.g., "Los Angeles Lakers")
  "abbreviation" TEXT,        -- Shortened team name (e.g., "LAL")
  "nickname" TEXT,            -- Commonly used nickname for the team (e.g., "Lakers")
  "city" TEXT,                -- City where the team is based
  "state" TEXT,               -- State where the team is located
  "year_founded" REAL         -- Year the team was established
);

game Table
Contains detailed statistics for each NBA game, including home and away team performance.
CREATE TABLE IF NOT EXISTS "game" (
  "season_id" TEXT,            -- Season identifier, formatted as "2YYYY" (e.g., "21970" for the 1970 season)
  "team_id_home" TEXT,         -- ID of the home team (matches "id" in team table)
  "team_abbreviation_home" TEXT, -- Abbreviation of the home team
  "team_name_home" TEXT,       -- Full name of the home team
  "game_id" TEXT PRIMARY KEY,  -- Unique identifier for the game
  "game_date" TIMESTAMP,       -- Date the game was played (YYYY-MM-DD format)
  "matchup_home" TEXT,         -- Matchup details including opponent (e.g., "LAL vs. BOS")
  "wl_home" TEXT,              -- "W" if the home team won, "L" if they lost
  "min" INTEGER,               -- Total minutes played in the game
  "fgm_home" REAL,             -- Field goals made by the home team
  "fga_home" REAL,             -- Field goals attempted by the home team
  "fg_pct_home" REAL,          -- Field goal percentage of the home team
  "fg3m_home" REAL,            -- Three-point field goals made by the home team
  "fg3a_home" REAL,            -- Three-point attempts by the home team
  "fg3_pct_home" REAL,         -- Three-point field goal percentage of the home team
  "ftm_home" REAL,             -- Free throws made by the home team
  "fta_home" REAL,             -- Free throws attempted by the home team
  "ft_pct_home" REAL,          -- Free throw percentage of the home team
  "oreb_home" REAL,            -- Offensive rebounds by the home team
  "dreb_home" REAL,            -- Defensive rebounds by the home team
  "reb_home" REAL,             -- Total rebounds by the home team
  "ast_home" REAL,             -- Assists by the home team
  "stl_home" REAL,             -- Steals by the home team
  "blk_home" REAL,             -- Blocks by the home team
  "tov_home" REAL,             -- Turnovers by the home team
  "pf_home" REAL,              -- Personal fouls by the home team
  "pts_home" REAL,             -- Total points scored by the home team
  "plus_minus_home" INTEGER,   -- Plus/minus rating for the home team
  "video_available_home" INTEGER, -- Indicates whether video is available (1 = Yes, 0 = No)
  "team_id_away" TEXT,         -- ID of the away team
  "team_abbreviation_away" TEXT, -- Abbreviation of the away team
  "team_name_away" TEXT,       -- Full name of the away team
  "matchup_away" TEXT,         -- Matchup details from the away team’s perspective
  "wl_away" TEXT,              -- "W" if the away team won, "L" if they lost
  "fgm_away" REAL,             -- Field goals made by the away team
  "fga_away" REAL,             -- Field goals attempted by the away team
  "fg_pct_away" REAL,          -- Field goal percentage of the away team
  "fg3m_away" REAL,            -- Three-point field goals made by the away team
  "fg3a_away" REAL,            -- Three-point attempts by the away team
  "fg3_pct_away" REAL,         -- Three-point field goal percentage of the away team
  "ftm_away" REAL,             -- Free throws made by the away team
  "fta_away" REAL,             -- Free throws attempted by the away team
  "ft_pct_away" REAL,          -- Free throw percentage of the away team
  "oreb_away" REAL,            -- Offensive rebounds by the away team
  "dreb_away" REAL,            -- Defensive rebounds by the away team
  "reb_away" REAL,             -- Total rebounds by the away team
  "ast_away" REAL,             -- Assists by the away team
  "stl_away" REAL,             -- Steals by the away team
  "blk_away" REAL,             -- Blocks by the away team
  "tov_away" REAL,             -- Turnovers by the away team
  "pf_away" REAL,              -- Personal fouls by the away team
  "pts_away" REAL,             -- Total points scored by the away team
  "plus_minus_away" INTEGER,   -- Plus/minus rating for the away team
  "video_available_away" INTEGER, -- Indicates whether video is available (1 = Yes, 0 = No)
  "season_type" TEXT           -- Regular season or playoffs
);

other_stats Table
Stores additional game statistics, linked to the game table via game_id.
CREATE TABLE IF NOT EXISTS "other_stats" (
  "game_id" TEXT,             -- Unique game identifier (links to "game" table)
  "league_id" TEXT,           -- League identifier
  "team_id_home" TEXT,        -- Home team identifier
  "team_abbreviation_home" TEXT, -- Home team abbreviation
  "team_city_home" TEXT,      -- Home team city
  "pts_paint_home" INTEGER,   -- Points in the paint by the home team
  "pts_2nd_chance_home" INTEGER, -- Second chance points by the home team
  "pts_fb_home" INTEGER,      -- Fast break points by the home team
  "largest_lead_home" INTEGER,-- Largest lead by the home team
  "lead_changes" INTEGER,     -- Number of lead changes in the game
  "times_tied" INTEGER,       -- Number of times the score was tied
  "team_turnovers_home" INTEGER, -- Home team turnovers
  "total_turnovers_home" INTEGER, -- Total turnovers in the game
  "team_rebounds_home" INTEGER, -- Home team rebounds
  "pts_off_to_home" INTEGER,  -- Points off turnovers by the home team
  "team_id_away" TEXT,        -- Away team identifier
  "pts_paint_away" INTEGER,   -- Points in the paint by the away team
  "pts_2nd_chance_away" INTEGER, -- Second chance points by the away team
  "pts_fb_away" INTEGER,      -- Fast break points by the away team
  "largest_lead_away" INTEGER,-- Largest lead by the away team
  "team_turnovers_away" INTEGER, -- Away team turnovers
  "total_turnovers_away" INTEGER, -- Total turnovers in the game
  "team_rebounds_away" INTEGER, -- Away team rebounds
  "pts_off_to_away" INTEGER   -- Points off turnovers by the away team
);


Team Name Information
In the plaintext user questions, only the full team names will be used, but in the queries you may use the full team names or the abbreviations. 
The full team names can be used with the game table, while the abbreviations should be used with the other_stats table.
Notice they are separated by the | character in the following list:

Atlanta Hawks|ATL
Boston Celtics|BOS
Cleveland Cavaliers|CLE
New Orleans Pelicans|NOP
Chicago Bulls|CHI
Dallas Mavericks|DAL
Denver Nuggets|DEN
Golden State Warriors|GSW
Houston Rockets|HOU
Los Angeles Clippers|LAC
Los Angeles Lakers|LAL
Miami Heat|MIA
Milwaukee Bucks|MIL
Minnesota Timberwolves|MIN
Brooklyn Nets|BKN
New York Knicks|NYK
Orlando Magic|ORL
Indiana Pacers|IND
Philadelphia 76ers|PHI
Phoenix Suns|PHX
Portland Trail Blazers|POR
Sacramento Kings|SAC
San Antonio Spurs|SAS
Oklahoma City Thunder|OKC
Toronto Raptors|TOR
Utah Jazz|UTA
Memphis Grizzlies|MEM
Washington Wizards|WAS
Detroit Pistons|DET
Charlotte Hornets|CHA



Query Guidelines
Use team_name_home and team_name_away to match teams.

To filter by season, use season_id = '2YYYY'.

Example: To get games from 2005, use season_id = '22005'. To get games from 1972, use season_id = "21972". To get games from 2015, use season_id = "22015".

The game_id column links the game and other_stats tables.

Ensure queries return relevant columns and avoid unnecessary joins.

Example User Requests and SQLite Queries
Request:
"What is the most points the Los Angeles Lakers have ever scored at home?"
SQLite:
SELECT MAX(pts_home) 
FROM game 
WHERE team_name_home = 'Los Angeles Lakers';

Request:
"How many points did the Miami Heat score on January 10, 2010?"
SQLite:
SELECT team_name_home, pts_home, team_name_away, pts_away 
FROM game 
WHERE DATE(game_date) = '2010-01-10' 
AND (team_name_home = 'Miami Heat' OR team_name_away = 'Miami Heat');

Request:
"Which team won the most home games in the 2000 season?"
SQLite:
SELECT team_name_home, COUNT(*) AS wins
FROM game
WHERE wl_home = 'W' AND season_id = '22000'
GROUP BY team_name_home
ORDER BY wins DESC
LIMIT 1;

Generate only the SQLite query prefaced by SQLite: and no other text, do not output an explanation of the query. Now generate an SQLite query for the following question: """

## Test model performance on a single example

In [4]:
# Create message with sample query and run model
message=[{ 'role': 'user', 'content': input_text + sample["natural_query"].values[0]}]
inputs = tokenizer.apply_chat_template(message, add_generation_prompt=True, return_tensors="pt").to(model.device)
outputs = model.generate(inputs, max_new_tokens=512, do_sample=False, top_k=50, top_p=0.95, num_return_sequences=1, eos_token_id=tokenizer.eos_token_id)

# Print output
query_output = tokenizer.decode(outputs[0][len(inputs[0]):], skip_special_tokens=True)
print(query_output)

c:\Users\Dean\AppData\Local\Programs\Python\Python312\Lib\site-packages\transformers\generation\configuration_utils.py:634: UserWarning: `do_sample` is set to `False`. However, `top_p` is set to `0.95` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `top_p`.
  warnings.warn(
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:32021 for open-end generation.
The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
c:\Users\Dean\AppData\Local\Programs\Python\Python312\Lib\site-packages\transformers\integrations\sdpa_attention.py:53: UserWarning: 1Torch was not compiled with flash attention. (Triggered i

SQLite:
SELECT MAX(largest_lead_home) 
FROM other_stats 
WHERE team_name_home = 'Golden State Warriors' AND season_id = '22018';



# Test sample output on sqlite3 database

In [5]:
import sqlite3 as sql

# Create connection to sqlite3 database
connection = sql.connect('./nba-data/nba.sqlite')
cursor = connection.cursor()

# Execute query from model output and print result
if query_output[0:7] == "SQLite:":
    print("cleaned")
    query = query_output[7:]
elif query_output[0:4] == "SQL:":
    query = query_output[4:]
else:
    query = query_output
cursor.execute(query)
rows = cursor.fetchall()
for row in rows:
    print(row)

cleaned


OperationalError: no such column: team_name_home

## Create function to compare output to ground truth result from examples

In [17]:
def compare_result(sample_query, sample_result, query_output):
    # Clean model output to only have the query output
    if query_output[0:7] == "SQLite:":
        query = query_output[7:]
    elif query_output[0:4] == "SQL:":
        query = query_output[4:]
    else:
        query = query_output
    
    # Try to execute query, if it fails, then this is a failure of the model
    try:
        # Execute query and obtain result
        cursor.execute(query)
        rows = cursor.fetchall()

        # Strip all whitespace before comparing queries since there may be differences in spacing, newlines, tabs, etc.
        query = query.replace(" ", "").replace("\n", "").replace("\t", "")
        sample_query = sample_query.replace(" ", "").replace("\n", "").replace("\t", "")
        query_match = (query == sample_query)

        # Check if this is a multi-line query
        if "|" in sample_result or "(" in sample_result:
            if "(" in sample_result:
                sample_result = sample_result.replace("(", "").replace(")", "")
                result_list = sample_result.split(",") 
            else:
                result_list = sample_result.split("|") 

            for i in range(len(result_list)):
                result_list[i] = str(result_list[i]).strip()
            result = False
            for row in rows:
                for r in row:
                    if str(r) in result_list:
                        return query_match, True
            if len(rows) == 1:
                for r in rows[0]:
                    if r == str(len(result_list)):
                        return query_match, True
            return query_match, result
        else:
            print(rows)
            result = False
            for row in rows:
                for r in row:
                    if str(r) in str(sample_result):
                        return query_match, True

            # Compare results and return
            return query_match, result
    except:
        return False, False

# Obtain sample
sample = df.sample(n=1)
print(sample["natural_query"].values[0])
print(sample["sql_query"].values[0])
print(sample["result"].values[0])

# Create message with sample query and run model
message=[{ 'role': 'user', 'content': input_text + sample["natural_query"].values[0]}]
inputs = tokenizer.apply_chat_template(message, add_generation_prompt=True, return_tensors="pt").to(model.device)
outputs = model.generate(inputs, max_new_tokens=512, do_sample=False, top_k=50, top_p=0.95, num_return_sequences=1, eos_token_id=tokenizer.eos_token_id)

# Print output
query_output = tokenizer.decode(outputs[0][len(inputs[0]):], skip_special_tokens=True)
print(query_output)

result = compare_result(sample["sql_query"].values[0], sample["result"].values[0], query_output)
print("SQL matched? " + str(result[0]))
print("Result matched? " + str(result[1]))

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:32021 for open-end generation.


How many games had at least one team with 30+ assists?
SELECT COUNT(*)  FROM game  WHERE ast_home >= 30 OR ast_away >= 30;
11305
SQLite:
SELECT COUNT(*) 
FROM game 
WHERE ast_home >= 30 OR ast_away >= 30;

[(11305,)]
SQL matched? True
Result matched? True
